In [25]:
import numpy as np, pandas as pd, plotly.express as px, plotly.graph_objects as go
from scipy.signal import savgol_filter as sgf
from pathlib import Path
import scipy.optimize as opt

from SJ_Haar_CNV import base_search
from SJ_Haar_CNV import decomposition
from SJ_Haar_CNV import report
from tests import test_data
np.random.seed(2)

# Generate Toy Data
We make some simulated data with 5 segments. 3 of them are the same mean, and 2 of the segments are alterations. One of them is a focal, drastic change in mean and the latter is a large, minute change in mean. 
We add noise to the data from a normal distribution with a standard deviation equal to the magnitude of alteration 3. This makes that segment difficult to detect.
Finally, we added a small section of much higher noise in the first signal.

In [26]:
base_dist = [np.repeat (5,1800), np.repeat (-6,210), np.repeat (5,1900), np.repeat (6,1900), np.repeat(5,1000)]
true_signal = np.concatenate(base_dist)
noise = np.random.normal(0,1,true_signal.size)
noise[500:1000] = np.random.normal(0,1.5,500) # <- uncomment this later
noisy_signal = true_signal + noise
types = [np.repeat(f'mean_{i}', j.size) for i,j in enumerate(base_dist)]

In [27]:
df = pd.DataFrame({'true_signal':true_signal,'raw':noisy_signal,'segment':np.concatenate(types)})
df

true_signal       raw segment
0               5  4.583242  mean_0
1               5  4.943733  mean_0
2               5  2.863804  mean_0
3               5  6.640271  mean_0
4               5  3.206564  mean_0
...           ...       ...     ...
6805            5  4.778086  mean_4
6806            5  4.941878  mean_4
6807            5  4.816082  mean_4
6808            5  5.102196  mean_4
6809            5  7.822525  mean_4

[6810 rows x 3 columns]

In [28]:
fig = px.scatter(df, x = df.index, y = 'raw', color = 'segment', title = 'Simulated Data with Means marked')
fig.add_annotation(x=4800, y = -2, text = "Slight mean shift ^", showarrow = False)
# fig.add_trace(go.Scatter(x = df.index, y = true_signal, mode = 'lines', name = 'True Signal',zorder=-2))
fig.show()

# With the data in hand, here are the steps we need to create our results

In [29]:
basis = base_search.generate_haar_basis(df['raw'], p0=.8, length = 21, debug = False)

In [30]:
basis_matrix, filtered_coefficients, all_coefficients, threshold, rle_y = decomposition.decompose (df['raw'].values, basis)
df['transformed'] = decomposition.rle_to_array(rle_y)

In [31]:
fig = go.Figure()
fig.add_trace (go.Scatter (y = df['true_signal'], name = 'true signal'))
##like a twwinx in matplotlib? so the scales are separate?
for i in np.where(filtered_coefficients)[0]:
    fig.add_trace (go.Scatter (x = np.arange (basis[i][2], basis[i][2] + basis[i][3][1]+basis[i][4][1]),
                               y = 10*decomposition.generate_wavelet_function (basis[i]),
                               name = 'wavelet ' + str(i)))

fig.show()

The "power spectrum" of the wavelets

In [32]:
fig = go.Figure()
fig.add_trace (go.Scatter (x = np.sort(np.abs(all_coefficients)),
                           y = np.linspace (0,1, len(all_coefficients)), mode = 'markers'))
fig.add_vline(x = threshold, line_dash = 'dash')

In [33]:
fig = report.visualize_data(df)
fig

This visualization is returned as a basic plotly figure object, so it can be edited afterwards too.

In [34]:
fig.add_trace(go.Scatter(x = df.index, y = df['true_signal'], mode = 'lines', name = 'Original Signal', line={'color':'black'}))

We also have special support for inhomogenous data. You may provide the relative positions of segments to the visualization step

In [35]:
locations = np.array(df.index)
locations[3500:] = locations[3500:] + 500
df['location'] = locations

In [36]:
report.visualize_data(df)

Currently the visualization just extends the noise estimation and segment call across the barriers, but in the future that could be remedied.